In [13]:
import pandas as pd
import plotly.graph_objs as go
from plotly.subplots import make_subplots

# Load the data
df = pd.read_csv('tau_grads.csv')

# Create a plotly interactive plot
fig = make_subplots(rows=1, cols=1)

# Adding traces for each column against the index
for column in df.columns:
    if column != 'tau':  # Assuming 'tau' is not to be plotted against index but as part of the data
        fig.add_trace(go.Scatter(x=df.index, y=df[column], mode='lines', name=column))

# Update layout for better visualization
fig.update_layout(
    title='Time Series Data Visualization Against Index',
    xaxis_title='Index (Time)',
    yaxis_title='Values',
    legend_title='Metrics',
    hovermode='x unified'
)

# Show plot
fig.show()


In [14]:
df['ratio'] = df['regularized_grad_norm'] / df['original_grad_norm']
df['ratio_last_new'] = df['regul_last_new'] / df['original_last_new']
df['ratio_last_known'] = df['regul_last_known'] / df['original_last_known']
df.fillna(0, inplace=True)

# Create a plotly interactive plot
fig = make_subplots(rows=1, cols=1)

# Adding traces for each column against the index
for column in ['ratio', 'ratio_last_new', 'ratio_last_known']:
    fig.add_trace(go.Scatter(x=df.index, y=df[column], mode='lines', name=column))

# Update layout for better visualization
fig.update_layout(
    title='Ratios of Regularized to Original Metrics',
    xaxis_title='Index (Time)',
    yaxis_title='Values',
    legend_title='Metrics',
    hovermode='x unified'
)

# Show plot
fig.show()

In [15]:
#plot tau values
fig = make_subplots(rows=1, cols=1)

# Adding traces for each column against the index
for column in ['tau']:
    fig.add_trace(go.Scatter(x=df.index, y=df[column], mode='lines', name=column))

# Update layout for better visualization
fig.update_layout(
    title='Tau values',
    xaxis_title='Index (Time)',
    yaxis_title='Values',
    legend_title='Metrics',
    hovermode='x unified'
)

# Show plot
fig.show()


In [16]:
import torch 

# Matrix size
n = 10
epsilon = 0.001

# Create a random gradient (with both positive and negative elements)
gradient = torch.randn(n)

# Compute the outer product and add small epsilon to its diagonal
A = torch.outer(gradient, gradient)
A += epsilon * torch.eye(n)  # Add epsilon to the diagonal to make it well-conditioned
g = torch.randn(n)

# Method 1: Using torch.linalg.lstsq
lstsq_result = torch.linalg.lstsq(A, g)
x_lstsq = lstsq_result.solution
res = lstsq_result.residuals

# Method 2: Using torch.mm(A.inverse()) @ g
A_inv = torch.inverse(A)
x_mm = torch.mm(A_inv, g.view(-1, 1)).view(-1)

#Method 3: Using torch.linalg.solve
x_solve = torch.linalg.solve(A, g)

# Calculate relative difference between the two solutions
relative_error = torch.norm(x_lstsq - x_mm) / torch.norm(x_lstsq)

# Display the relative error
print(relative_error.item())
print(x_lstsq)
print(x_mm)
print(x_solve)

2.4989143639686517e-05
tensor([ -282.3876,  -627.4522,  1369.4442,  -716.7456, -1310.3043,    53.2670,
          258.5035,   262.1505,  -963.9951, -1037.4597])
tensor([ -282.4371,  -627.4604,  1369.4207,  -716.7556, -1310.3151,    53.2874,
          258.4843,   262.1605,  -963.9905, -1037.4568])
tensor([ -282.4370,  -627.4603,  1369.4210,  -716.7556, -1310.3153,    53.2874,
          258.4843,   262.1603,  -963.9905, -1037.4569])
